# What is the notebook about?

## Problem - Taxi Environment Algorithms
This problem deals with a taxi environment and stochastic actions. The tasks you have to do are:
- Implement Policy Iteration
- Implement Modified Policy Iteration
- Implement Value Iteration
- Implement Gauss Seidel Value Iteration
- Visualize the results
- Explain the results

## How to use this notebook? 📝

- This is a shared template and any edits you make here will not be saved.**You
should make a copy in your own drive**. Click the "File" menu (top-left), then "Save a Copy in Drive". You will be working in your copy however you like.

- **Update the config parameters**. You can define the common variables here

Variable | Description
--- | ---
`AICROWD_DATASET_PATH` | Path to the file containing test data. This should be an absolute path.
`AICROWD_RESULTS_DIR` | Path to write the output to.
`AICROWD_ASSETS_DIR` | In case your notebook needs additional files (like model weights, etc.,), you can add them to a directory and specify the path to the directory here (please specify relative path). The contents of this directory will be sent to AIcrowd for evaluation.
`AICROWD_API_KEY` | In order to submit your code to AIcrowd, you need to provide your account's API key. This key is available at https://www.aicrowd.com/participants/me

- **Installing packages**. Please use the [Install packages 🗃](#install-packages-) section to install the packages

# Setup AIcrowd Utilities 🛠

We use this to bundle the files for submission and create a submission on AIcrowd. Do not edit this block.

In [99]:
!pip install aicrowd-cli > /dev/null 

# AIcrowd Runtime Configuration 🧷

Get login API key from https://www.aicrowd.com/participants/me

In [100]:
import os

AICROWD_DATASET_PATH = os.getenv("DATASET_PATH", os.getcwd()+"/13d77bb0-b325-4e95-a03b-833eb6694acd_a2_taxi_inputs.zip")
AICROWD_RESULTS_DIR = os.getenv("OUTPUTS_DIR", "results")


API Key valid
Saved API Key successfully!
13d77bb0-b325-4e95-a03b-833eb6694acd_a2_taxi_inputs.zip: 100% 31.2k/31.2k [00:00<00:00, 279kB/s]


In [ ]:
!unzip $AICROWD_DATASET_PATH

Archive:  /content/13d77bb0-b325-4e95-a03b-833eb6694acd_a2_taxi_inputs.zip
replace inputs/inputs_base.npy? [y]es, [n]o, [A]ll, [N]one, [r]ename: 

In [ ]:
DATASET_DIR = 'inputs/'

## Taxi Environment

Read the environment to understand the functions, but do not edit anything

In [ ]:
import numpy as np
import pandas as pd
class TaxiEnv_HW2:
    def __init__(self, states, actions, probabilities, rewards, initial_policy):
        self.possible_states = states
        self._possible_actions = {st: ac for st, ac in zip(states, actions)}
        self._ride_probabilities = {st: pr for st, pr in zip(states, probabilities)}
        self._ride_rewards = {st: rw for st, rw in zip(states, rewards)}
        self.initial_policy = initial_policy
        self._verify()

    def _check_state(self, state):
        assert state in self.possible_states, "State %s is not a valid state" % state

    def _verify(self):
        """ 
        Verify that data conditions are met:
        Number of actions matches shape of next state and actions
        Every probability distribution adds up to 1 
        """
        ns = len(self.possible_states)
        for state in self.possible_states:
            ac = self._possible_actions[state]
            na = len(ac)

            rp = self._ride_probabilities[state]
            assert np.all(rp.shape == (na, ns)), "Probabilities shape mismatch"
        
            rr = self._ride_rewards[state]
            assert np.all(rr.shape == (na, ns)), "Rewards shape mismatch"

            assert np.allclose(rp.sum(axis=1), 1), "Probabilities don't add up to 1"

    def possible_actions(self, state):
        """ Return all possible actions from a given state """
        self._check_state(state)
        return self._possible_actions[state]

    def ride_probabilities(self, state, action):
        """ 
        Returns all possible ride probabilities from a state for a given action
        For every action a list with the returned with values in the same order as self.possible_states
        """
        actions = self.possible_actions(state)
        ac_idx = actions.index(action)
        return self._ride_probabilities[state][ac_idx]

    def ride_rewards(self, state, action):
        actions = self.possible_actions(state)
        ac_idx = actions.index(action)
        return self._ride_rewards[state][ac_idx]

## Example of Environment usage

In [ ]:
def check_taxienv():
    # These are the values as used in the pdf, but they may be changed during submission, so do not hardcode anything

    states = ['A', 'B', 'C']

    actions = [['1','2','3'], ['1','2'], ['1','2','3']]

    probs = [np.array([[1/2,  1/4,  1/4],
                    [1/16, 3/4,  3/16],
                    [1/4,  1/8,  5/8]]),

            np.array([[1/2,   0,     1/2],
                    [1/16,  7/8,  1/16]]),

            np.array([[1/4,  1/4,  1/2],
                    [1/8,  3/4,  1/8],
                    [3/4,  1/16, 3/16]]),]

    rewards = [np.array([[10,  4,  8],
                        [ 8,  2,  4],
                        [ 4,  6,  4]]),

            np.array([[14,  0, 18],
                        [ 8, 16,  8]]),

            np.array([[10,  2,  8],
                        [6,   4,  2],
                        [4,   0,  8]]),]
    initial_policy = {'A': '1', 'B': '1', 'C': '1'}

    env = TaxiEnv_HW2(states, actions, probs, rewards, initial_policy)
    print("All possible states", env.possible_states)
    print("All possible actions from state B", env.possible_actions('B'))
    print("Ride probabilities from state A with action 2", env.ride_probabilities('A', '2'))
    print("Ride rewards from state C with action 3", env.ride_rewards('C', '3'))

    base_kwargs = {"states": states, "actions": actions, 
                "probabilities": probs, "rewards": rewards,
                "initial_policy": initial_policy}
    return base_kwargs

base_kwargs = check_taxienv()
env = TaxiEnv_HW2(**base_kwargs)

## Task 1 - Policy Iteration
Run policy iteration on the environment and generate the policy and expected reward

In [ ]:
# 1.1 Policy Iteration
def policy_iteration(taxienv, gamma):
    # A list of all the states
    states = taxienv.possible_states
    # Initial values
    values = {s: 0 for s in states}

    # This is a dictionary of states to policies -> e.g {'A': '1', 'B': '2', 'C': '1'}
    policy = taxienv.initial_policy.copy()

    ## Begin code here

    # Hints - 
    # Do not hardcode anything
    # Only the final result is required for the results
    # Put any extra data in "extra_info" dictonary for any plots etc
    # Use the helper functions taxienv.ride_rewards, taxienv.ride_probabilities,  taxienv.possible_actions
    # For terminating condition use the condition exactly mentioned in the pdf

    while True:
      while True:
        delta = 0
        for s in states:
          j = values[s]
          rew = 0
          for (prob,ns,reward) in zip(taxienv.ride_probabilities(s,policy[s]),states,taxienv.ride_rewards(s,policy[s])):
            rew += prob*(reward + gamma*values[ns])
          values[s] = rew
          absv = values[s] - j
          if (absv<0):
            absv = -absv
          if (delta < absv):
            delta = absv
        if (delta < 0.00000001):
          break
      done = 1
      for s in states:
        b = policy[s]
        mxc = np.NINF
        for act in taxienv.possible_actions(s):
          cost = 0
          for (prob,ns,reward) in zip(taxienv.ride_probabilities(s,act),states,taxienv.ride_rewards(s,act)):
            cost += prob*(reward + gamma*values[ns])
          if (mxc < cost):
            mxc = cost
            policy[s] = act
        if (b != policy[s]):
          done = 0
      if (done == 1):
        break
            

    
    # Put your extra information needed for plots etc in this dictionary
    extra_info = {}

    ## Do not edit below this line

    # Final results
    return {"Expected Reward": values, "Policy": policy}, extra_info

# Task 2 - Policy Iteration for multiple values of gamma

Ideally this code should run as is

In [ ]:
# 1.2 Policy Iteration with different values of gamma
def run_policy_iteration(env):
    gamma_values = np.arange(5, 100, 5)/100
    results, extra_info = {}, {}
    for gamma in gamma_values:
        results[gamma], extra_info[gamma] = policy_iteration(env, gamma)
    return results, extra_info

results, extra_info = run_policy_iteration(env)

# Task 3 - Modifed Policy Iteration

Implement modified policy iteration (where Value iteration is done for fixed m number of steps)

In [ ]:
# 1.3 Modified Policy Iteration
def modified_policy_iteration(taxienv, gamma, m):
    # A list of all the states
    states = taxienv.possible_states
    # Initial values
    values = {s: 0 for s in states}

    # This is a dictionary of states to policies -> e.g {'A': '1', 'B': '2', 'C': '1'}
    policy = taxienv.initial_policy.copy()

    ## Begin code here

    # Hints - 
    # Do not hardcode anything
    # Only the final result is required for the results
    # Put any extra data in "extra_info" dictonary for any plots etc
    # Use the helper functions taxienv.ride_rewards, taxienv.ride_probabilities,  taxienv.possible_actions
    # For terminating condition use the condition exactly mentioned in the pdf

    while True:
      for k in range(m):
        copy_new = {}
        for s in states:
          rew = 0
          for (prob,ns,reward) in zip(taxienv.ride_probabilities(s,policy[s]),states,taxienv.ride_rewards(s,policy[s])):
            rew += prob*(reward + gamma*values[ns])
          copy_new[s] = rew
        for s in states:
          values[s] = copy_new[s]
      done = 1
      for s in states:
        b = policy[s]
        mxc = np.NINF
        for act in taxienv.possible_actions(s):
          cost = 0
          for (prob,ns,reward) in zip(taxienv.ride_probabilities(s,act),states,taxienv.ride_rewards(s,act)):
            cost += prob*(reward + gamma*values[ns])
          if (mxc < cost):
            mxc = cost
            policy[s] = act
        if (b != policy[s]):
          done = 0
      if (done == 1):
        break


    # Put your extra information needed for plots etc in this dictionary
    extra_info = {}

    ## Do not edit below this line


    # Final results
    return {"Expected Reward": values, "Policy": policy}, extra_info

# Task 4 Modified policy iteration for multiple values of m

Ideally this code should run as is

In [ ]:
def run_modified_policy_iteration(env):
    m_values = np.arange(1, 15)
    gamma = 0.9
    results, extra_info = {}, {}
    for m in m_values:
        results[m], extra_info[m] = modified_policy_iteration(env, gamma, m)
    return results, extra_info

results, extra_info = run_modified_policy_iteration(env)

# Task 5 Value Iteration

Implement value iteration and find the policy and expected rewards

In [ ]:
# 1.4 Value Iteration
def value_iteration(taxienv, gamma):
    # A list of all the states
    states = taxienv.possible_states
    # Initial values
    values = {s: 0 for s in states}

    # This is a dictionary of states to policies -> e.g {'A': '1', 'B': '2', 'C': '1'}
    policy = taxienv.initial_policy.copy()

    ## Begin code here

    # Hints - 
    # Do not hardcode anything
    # Only the final result is required for the results
    # Put any extra data in "extra_info" dictonary for any plots etc
    # Use the helper functions taxienv.ride_rewards, taxienv.ride_probabilities,  taxienv.possible_actions
    # For terminating condition use the condition exactly mentioned in the pdf

    while True:
      delta = 0
      H = {s: np.NINF for s in states}
      for s in states:
        mxc = np.NINF
        for act in taxienv.possible_actions(s):
          cost = 0
          for (prob,ns,reward) in zip(taxienv.ride_probabilities(s,act),states,taxienv.ride_rewards(s,act)):
            cost += prob*(reward + gamma*values[ns])
          if (mxc < cost):
            mxc = cost
            policy[s] = act
        H[s] = mxc
        absv = values[s] - H[s]
        if (absv<0):
          absv = -absv
        if (delta < absv):
          delta = absv
      for s in states:
        values[s] = H[s]
      if (delta < 0.00000001):
        break


    # Put your extra information needed for plots etc in this dictionary
    extra_info = {}

    ## Do not edit below this line

    # Final results
    return {"Expected Reward": values, "Policy": policy}, extra_info

# Task 6 Value Iteration with multiple values of gamma

Ideally this code should run as is

In [ ]:
def run_value_iteration(env):
    gamma_values = np.arange(5, 100, 5)/100
    results = {}
    results, extra_info = {}, {}
    for gamma in gamma_values:
        results[gamma], extra_info[gamma] = value_iteration(env, gamma)
    return results, extra_info
  
results, extra_info = run_value_iteration(env)

# Task 7 Gauss Seidel Value Iteration

Implement Gauss Seidel Value Iteration

In [ ]:
# 1.4 Gauss Seidel Value Iteration
def gauss_seidel_value_iteration(taxienv, gamma):
    # A list of all the states
    # For Gauss Seidel Value Iteration - iterate through the values in the same order
    states = taxienv.possible_states

    # Initial values
    values = {s: 0 for s in states}

    # This is a dictionary of states to policies -> e.g {'A': '1', 'B': '2', 'C': '1'}
    policy = taxienv.initial_policy.copy()

    # Hints - 
    # Do not hardcode anything
    # For Gauss Seidel Value Iteration - iterate through the values in the same order as taxienv.possible_states
    # Only the final result is required for the results
    # Put any extra data in "extra_info" dictonary for any plots etc
    # Use the helper functions taxienv.ride_rewards, taxienv.ride_probabilities,  taxienv.possible_actions
    # For terminating condition use the condition exactly mentioned in the pdf

    ## Begin code here
    
    while True:
      delta = 0
      for s in states:
        mxc = np.NINF
        j = values[s]
        for act in taxienv.possible_actions(s):
          cost = 0
          for (prob,ns,reward) in zip(taxienv.ride_probabilities(s,act),states,taxienv.ride_rewards(s,act)):
            cost += prob*(reward + gamma*values[ns])
          if (mxc < cost):
            mxc = cost
            policy[s] = act
        values[s] = mxc
        absv = j - values[s]
        if (absv<0):
          absv = -absv
        if (delta < absv):
          delta = absv
      if (delta < 0.00000001):
        break

    # Put your extra information needed for plots etc in this dictionary
    extra_info = {}

    ## Do not edit below this line

    # Final results
    return {"Expected Reward": values, "Policy": policy}, extra_info

# Task 8 Gauss Seidel Value Iteration with multiple values of gamma

Ideally this code should run as is

In [ ]:
def run_gauss_seidel_value_iteration(env):
    gamma_values = np.arange(5, 100, 5)/100
    results = {}
    results, extra_info = {}, {}
    for gamma in gamma_values:
        results[gamma], extra_info[gamma] = gauss_seidel_value_iteration(env, gamma)
    return results, extra_info

results, extra_info = run_gauss_seidel_value_iteration(env)

# Generate Results ✅

In [ ]:
# Do not edit this cell
def get_results(kwargs):

    taxienv = TaxiEnv_HW2(**kwargs)

    policy_iteration_results = run_policy_iteration(taxienv)[0]
    modified_policy_iteration_results = run_modified_policy_iteration(taxienv)[0]
    value_iteration_results = run_value_iteration(taxienv)[0]
    gs_vi_results = run_gauss_seidel_value_iteration(taxienv)[0]

    final_results = {}
    final_results["policy_iteration"] = policy_iteration_results
    final_results["modifed_policy_iteration"] = modified_policy_iteration_results
    final_results["value_iteration"] = value_iteration_results
    final_results["gauss_seidel_iteration"] = gs_vi_results

    return final_results

In [ ]:
# Do not edit this cell, generate results with it as is
if not os.path.exists(AICROWD_RESULTS_DIR):
    os.mkdir(AICROWD_RESULTS_DIR)

for params_file in os.listdir(DATASET_DIR):
  kwargs = np.load(os.path.join(DATASET_DIR, params_file), allow_pickle=True).item()
  results = get_results(kwargs)
  idx = params_file.split('_')[-1][:-4]
  np.save(os.path.join(AICROWD_RESULTS_DIR, 'results_' + idx), results)

# Check your local score

This score is not your final score, and it doesn't use the marks weightages. This is only for your reference of how arrays are matched and with what tolerance.

In [ ]:
# Check your score on the given test cases (There are more private test cases not provided)
target_folder = 'targets'
result_folder = AICROWD_RESULTS_DIR

def check_algo_match(results, targets):
    param_matches = []
    for k in results:
        param_results = results[k]
        param_targets = targets[k]
        policy_match = param_results['Policy'] == param_targets['Policy']
        rv = [v for k, v in param_results['Expected Reward'].items()]
        tv = [v for k, v in param_targets['Expected Reward'].items()]
        rewards_match = np.allclose(rv, tv, rtol=3)
        equal = rewards_match and policy_match
        param_matches.append(equal)
    return np.mean(param_matches)

def check_score(target_folder, result_folder):
    match = []
    for out_file in os.listdir(result_folder):
        res_file = os.path.join(result_folder, out_file)
        results = np.load(res_file, allow_pickle=True).item()
        idx = out_file.split('_')[-1][:-4]  # Extract the file number
        target_file = os.path.join(target_folder, f"targets_{idx}.npy")
        targets = np.load(target_file, allow_pickle=True).item()
        algo_match = []
        for k in targets:
            algo_results = results[k]
            algo_targets = targets[k]
            algo_match.append(check_algo_match(algo_results, algo_targets))
        match.append(np.mean(algo_match))
    return np.mean(match)

if os.path.exists(target_folder):
    print("Shared data Score (normalized to 1):", check_score(target_folder, result_folder))

## Visualize results of Policy Iteration with multiple values of gamma


In [ ]:
## Visualize policy iteration with multiple values of gamma
results, extra_info = run_policy_iteration(env)
A = []
B = []
C = []
gamma_values = np.arange(5, 100, 5)/100
for g in gamma_values:
  A.append(results[g]['Expected Reward']['A'])
  B.append(results[g]['Expected Reward']['B'])
  C.append(results[g]['Expected Reward']['C'])

import matplotlib.pyplot as plt
plt.plot(gamma_values,A,label = 'state A')
plt.plot(gamma_values,B,label = 'state B')
plt.plot(gamma_values,C,label = 'state C')
plt.legend()

# Subjective questions


## 1.a How are values of $\gamma$ affecting results of policy iteration

<h1>
  Observations
<h1>

<ul>
  <li>
      The Expected reward is higher for higher values of gamma. Reason :  Positive rewards in the future would be exemplified with higher values of gamma.
  </li>
  <li>
      Smaller values of gamma seems to focus on a locally optimal choice while large values of gamma seems to give a more globally optimal solution. For extremely low values of gamma, the algorithm comes up with a greedy strategy virtually giving any meaningful weightage only to the first few stages. The policy then is {'A': '1', 'B': '1', 'C': '1'}. As gamma increases, the algorithm starts to take into account the long run rewards of the decision with increasing weightage and hence we see the shift in policy to {'A': '1', 'B': '2', 'C': '1'} and then to 	{'A': '1', 'B': '2', 'C': '2'} and finally to 	{'A': '2', 'B': '2', 'C': '2'}. Extremely large values of gamma will overshadow the current gain in the immediate step that follows and prioritizes the long run gain.
  </li>
</ul>


|                 | 0.05                                                                       | 0.1                                                                      | 0.15                                                                      | 0.2                                                                        | 0.25                                                                        | 0.3                                                                         | 0.35                                                                       | 0.4                                                                        | 0.45                                                                       | 0.5                                                                        | 0.55                                                                        | 0.6                                                                        | 0.65                                                                        | 0.7                                                                      | 0.75                                                                     | 0.8                                                                       | 0.85                                                                     | 0.9                                                                         | 0.95                                                                      |
|:----------------|:---------------------------------------------------------------------------|:-------------------------------------------------------------------------|:--------------------------------------------------------------------------|:---------------------------------------------------------------------------|:----------------------------------------------------------------------------|:----------------------------------------------------------------------------|:---------------------------------------------------------------------------|:---------------------------------------------------------------------------|:---------------------------------------------------------------------------|:---------------------------------------------------------------------------|:----------------------------------------------------------------------------|:---------------------------------------------------------------------------|:----------------------------------------------------------------------------|:-------------------------------------------------------------------------|:-------------------------------------------------------------------------|:--------------------------------------------------------------------------|:-------------------------------------------------------------------------|:----------------------------------------------------------------------------|:--------------------------------------------------------------------------|
| Expected Reward | {'A': 8.511527294546923, 'B': 16.400259909029575, 'C': 7.4988690667106095} | {'A': 9.076506149392834, 'B': 16.85636856362452, 'C': 8.050865123980312} | {'A': 9.708121492285777, 'B': 17.464503041460713, 'C': 8.669160453984542} | {'A': 10.437030074788021, 'B': 18.482142856612846, 'C': 9.384398496135692} | {'A': 11.274074073456447, 'B': 19.629629628834554, 'C': 10.207407407209406} | {'A': 12.243837242843748, 'B': 20.934065932820292, 'C': 11.162756162382273} | {'A': 13.378714434389575, 'B': 22.43076922849439, 'C': 12.282824024490601} | {'A': 14.722222218062745, 'B': 24.16666666169111, 'C': 13.611111109108625} | {'A': 16.334131265172196, 'B': 26.205533591380167, 'C': 15.20737070397659} | {'A': 18.29870129504681, 'B': 28.636363632167495, 'C': 17.155844153726775} | {'A': 20.789988634661945, 'B': 31.607396695666196, 'C': 19.830725213847188} | {'A': 24.025686438308284, 'B': 35.32772363825764, 'C': 23.458813102392277} | {'A': 28.276692060109887, 'B': 40.096280573890574, 'C': 28.129978785480258} | {'A': 34.06193076627213, 'B': 46.43541615340033, 'C': 34.36604101044906} | {'A': 42.31741138120016, 'B': 55.28505390685269, 'C': 43.10631739475281} | {'A': 55.079365046134924, 'B': 68.55820102458796, 'C': 56.26984124288862} | {'A': 77.24651210119615, 'B': 90.81170062152418, 'C': 78.43345572723322} | {'A': 121.65347105207364, 'B': 135.30627545205246, 'C': 122.83690301136426} | {'A': 255.02290826558783, 'B': 268.7646183427653, 'C': 256.2028492762011} |
| Policy          | {'A': '1', 'B': '1', 'C': '1'}                                             | {'A': '1', 'B': '1', 'C': '1'}                                           | {'A': '1', 'B': '2', 'C': '1'}                                            | {'A': '1', 'B': '2', 'C': '1'}                                             | {'A': '1', 'B': '2', 'C': '1'}                                              | {'A': '1', 'B': '2', 'C': '1'}                                              | {'A': '1', 'B': '2', 'C': '1'}                                             | {'A': '1', 'B': '2', 'C': '1'}                                             | {'A': '1', 'B': '2', 'C': '1'}                                             | {'A': '1', 'B': '2', 'C': '1'}                                             | {'A': '1', 'B': '2', 'C': '2'}                                              | {'A': '1', 'B': '2', 'C': '2'}                                             | {'A': '1', 'B': '2', 'C': '2'}                                              | {'A': '1', 'B': '2', 'C': '2'}                                           | {'A': '1', 'B': '2', 'C': '2'}                                           | {'A': '2', 'B': '2', 'C': '2'}                                            | {'A': '2', 'B': '2', 'C': '2'}                                           | {'A': '2', 'B': '2', 'C': '2'}                                              | {'A': '2', 'B': '2', 'C': '2'}                                            |

## 1.b For modified policy itetaration, do you find any improvement if you choose m=10.

<h1>
  Observations
<h1>

<ul>
  <li>
      The optimal policy is identical for all values of m. This is to be exepected as we are running the algorithm till it converges for every value of m.
  </li>
  <li>
      The expected reward for m = 10 is higher than m = 5. The expected reward is steadily increases with m and gets more closer to the optimal value of the reward. This is because the more number of times you run the iteration, the better the approximation of the expected reward of the given policy.
  </li>
</ul>


|                 | 1                                                            | 2                                                                          | 3                                                                       | 4                                                                        | 5                                                                         | 6                                                                       | 7                                                                           | 8                                                                           | 9                                                                           | 10                                                                         | 11                                                                         | 12                                                                        | 13                                                                          | 14                                                                          |
|:----------------|:-------------------------------------------------------------|:---------------------------------------------------------------------------|:------------------------------------------------------------------------|:-------------------------------------------------------------------------|:--------------------------------------------------------------------------|:------------------------------------------------------------------------|:----------------------------------------------------------------------------|:----------------------------------------------------------------------------|:----------------------------------------------------------------------------|:---------------------------------------------------------------------------|:---------------------------------------------------------------------------|:--------------------------------------------------------------------------|:----------------------------------------------------------------------------|:----------------------------------------------------------------------------|
| Expected Reward | {'A': 25.675390625, 'B': 39.27046874999999, 'C': 26.9415625} | {'A': 48.55490468521119, 'B': 62.203121287078865, 'C': 49.737400154724135} | {'A': 66.5070336319201, 'B': 80.16002669080505, 'C': 67.69034691854696} | {'A': 79.80001035898594, 'B': 93.45288211402925, 'C': 80.98345265619488} | {'A': 89.81178760453517, 'B': 103.46459982778873, 'C': 90.99521888644551} | {'A': 97.34789594613352, 'B': 111.0007013724186, 'C': 98.5313279386138} | {'A': 103.04102709136063, 'B': 116.69383160589359, 'C': 104.22445904173425} | {'A': 107.35314857748017, 'B': 121.00595299110296, 'C': 108.53658053027281} | {'A': 110.62884446690502, 'B': 124.28164886875567, 'C': 111.81227641956042} | {'A': 113.12458909097927, 'B': 126.77739349151406, 'C': 114.3080210436424} | {'A': 115.03191631274339, 'B': 128.68472071312897, 'C': 116.2153482654061} | {'A': 116.49414072619648, 'B': 130.1469451265653, 'C': 117.6775726788592} | {'A': 117.61874705064764, 'B': 131.27155145101457, 'C': 118.80217900331036} | {'A': 118.48653594228573, 'B': 132.13934034265242, 'C': 119.66996789494846} |
| Policy          | {'A': '2', 'B': '2', 'C': '2'}                               | {'A': '2', 'B': '2', 'C': '2'}                                             | {'A': '2', 'B': '2', 'C': '2'}                                          | {'A': '2', 'B': '2', 'C': '2'}                                           | {'A': '2', 'B': '2', 'C': '2'}                                            | {'A': '2', 'B': '2', 'C': '2'}                                          | {'A': '2', 'B': '2', 'C': '2'}                                              | {'A': '2', 'B': '2', 'C': '2'}                                              | {'A': '2', 'B': '2', 'C': '2'}                                              | {'A': '2', 'B': '2', 'C': '2'}                                             | {'A': '2', 'B': '2', 'C': '2'}                                             | {'A': '2', 'B': '2', 'C': '2'}                                            | {'A': '2', 'B': '2', 'C': '2'}                                              | {'A': '2', 'B': '2', 'C': '2'}                                              |

## 1.c Compare and contrast the behavior of Value Iteration and Gauss Seidel Value Iteraton

<h2>Gauss Seidel Value Iteration</h2>

|                 | 0.05                                                                       | 0.1                                                                      | 0.15                                                                    | 0.2                                                                      | 0.25                                                                       | 0.3                                                                         | 0.35                                                                    | 0.4                                                                         | 0.45                                                                      | 0.5                                                                        | 0.55                                                                      | 0.6                                                                       | 0.65                                                                       | 0.7                                                                      | 0.75                                                                     | 0.8                                                                      | 0.85                                                                     | 0.9                                                                         | 0.95                                                                      |
|:----------------|:---------------------------------------------------------------------------|:-------------------------------------------------------------------------|:------------------------------------------------------------------------|:-------------------------------------------------------------------------|:---------------------------------------------------------------------------|:----------------------------------------------------------------------------|:------------------------------------------------------------------------|:----------------------------------------------------------------------------|:--------------------------------------------------------------------------|:---------------------------------------------------------------------------|:--------------------------------------------------------------------------|:--------------------------------------------------------------------------|:---------------------------------------------------------------------------|:-------------------------------------------------------------------------|:-------------------------------------------------------------------------|:-------------------------------------------------------------------------|:-------------------------------------------------------------------------|:----------------------------------------------------------------------------|:--------------------------------------------------------------------------|
| Expected Reward | {'A': 8.511527294546923, 'B': 16.400259909029575, 'C': 7.4988690667106095} | {'A': 9.076506149392834, 'B': 16.85636856362452, 'C': 8.050865123980312} | {'A': 9.70812149293256, 'B': 17.464503042356245, 'C': 8.66916045411395} | {'A': 10.43703007363936, 'B': 18.48214285510763, 'C': 9.384398495833036} | {'A': 11.274074072135488, 'B': 19.62962962714145, 'C': 10.207407406785403} | {'A': 12.243837240938772, 'B': 20.934065930435885, 'C': 11.162756161665108} | {'A': 13.3787144345583, 'B': 22.43076922870161, 'C': 12.28282402456309} | {'A': 14.722222217898851, 'B': 24.166666661495807, 'C': 13.611111109029693} | {'A': 16.33413126434644, 'B': 26.20553359041331, 'C': 15.207370703537933} | {'A': 18.298701293837997, 'B': 28.63636363077955, 'C': 17.155844153026397} | {'A': 20.78998863222275, 'B': 31.60739669290458, 'C': 19.830725212339292} | {'A': 24.02568643692515, 'B': 35.32772363671855, 'C': 23.458813101474426} | {'A': 28.276692061545695, 'B': 40.09628057546244, 'C': 28.129978786496867} | {'A': 34.06193076743594, 'B': 46.43541615465501, 'C': 34.36604101132381} | {'A': 42.31741137784243, 'B': 55.28505390328474, 'C': 43.10631739208525} | {'A': 55.079365051578144, 'B': 68.5582010300939, 'C': 56.26984124730355} | {'A': 77.24651209951202, 'B': 90.81170061982581, 'C': 78.43345572578708} | {'A': 121.65347104963263, 'B': 135.30627544959796, 'C': 122.83690300915262} | {'A': 255.0229082673451, 'B': 268.7646183445272, 'C': 256.20284927787594} |
| Policy          | {'A': '1', 'B': '1', 'C': '1'}                                             | {'A': '1', 'B': '1', 'C': '1'}                                           | {'A': '1', 'B': '2', 'C': '1'}                                          | {'A': '1', 'B': '2', 'C': '1'}                                           | {'A': '1', 'B': '2', 'C': '1'}                                             | {'A': '1', 'B': '2', 'C': '1'}                                              | {'A': '1', 'B': '2', 'C': '1'}                                          | {'A': '1', 'B': '2', 'C': '1'}                                              | {'A': '1', 'B': '2', 'C': '1'}                                            | {'A': '1', 'B': '2', 'C': '1'}                                             | {'A': '1', 'B': '2', 'C': '2'}                                            | {'A': '1', 'B': '2', 'C': '2'}                                            | {'A': '1', 'B': '2', 'C': '2'}                                             | {'A': '1', 'B': '2', 'C': '2'}                                           | {'A': '1', 'B': '2', 'C': '2'}                                           | {'A': '2', 'B': '2', 'C': '2'}                                           | {'A': '2', 'B': '2', 'C': '2'}                                           | {'A': '2', 'B': '2', 'C': '2'}                                              | {'A': '2', 'B': '2', 'C': '2'}                                            |


<h2>Value Iteration</h2>

|                 | 0.05                                                                      | 0.1                                                                       | 0.15                                                                     | 0.2                                                                       | 0.25                                                                        | 0.3                                                                         | 0.35                                                                       | 0.4                                                                        | 0.45                                                                      | 0.5                                                                        | 0.55                                                                        | 0.6                                                                       | 0.65                                                                      | 0.7                                                                      | 0.75                                                                       | 0.8                                                                      | 0.85                                                                     | 0.9                                                                         | 0.95                                                                       |
|:----------------|:--------------------------------------------------------------------------|:--------------------------------------------------------------------------|:-------------------------------------------------------------------------|:--------------------------------------------------------------------------|:----------------------------------------------------------------------------|:----------------------------------------------------------------------------|:---------------------------------------------------------------------------|:---------------------------------------------------------------------------|:--------------------------------------------------------------------------|:---------------------------------------------------------------------------|:----------------------------------------------------------------------------|:--------------------------------------------------------------------------|:--------------------------------------------------------------------------|:-------------------------------------------------------------------------|:---------------------------------------------------------------------------|:-------------------------------------------------------------------------|:-------------------------------------------------------------------------|:----------------------------------------------------------------------------|:---------------------------------------------------------------------------|
| Expected Reward | {'A': 8.511527294182539, 'B': 16.400259908653545, 'C': 7.498869066334438} | {'A': 9.076506148654659, 'B': 16.856368562663413, 'C': 8.050865123013633} | {'A': 9.708121491779233, 'B': 17.46450304126533, 'C': 8.669160452818193} | {'A': 10.43703007317419, 'B': 18.482142855128945, 'C': 9.384398494226822} | {'A': 11.274074070814656, 'B': 19.629629626369894, 'C': 10.207407404147988} | {'A': 12.243837242020097, 'B': 20.934065932248725, 'C': 11.162756160939015} | {'A': 13.378714431634197, 'B': 22.43076922615468, 'C': 12.282824020675294} | {'A': 14.722222216827301, 'B': 24.16666666127172, 'C': 13.611111105716189} | {'A': 16.33413126569031, 'B': 26.20553359269582, 'C': 15.207370702310026} | {'A': 18.298701293190973, 'B': 28.636363630853307, 'C': 17.15584415033383} | {'A': 20.789988627490125, 'B': 31.607396689157056, 'C': 19.830725204761144} | {'A': 24.02568643325821, 'B': 35.327723634321096, 'C': 23.45881309401995} | {'A': 28.276692058162972, 'B': 40.09628057326413, 'C': 28.12997877946505} | {'A': 34.06193076174113, 'B': 46.43541615019445, 'C': 34.36604100170312} | {'A': 42.317411373067756, 'B': 55.28505390003232, 'C': 43.106317382312746} | {'A': 55.07936504724612, 'B': 68.55820102608209, 'C': 56.26984123772232} | {'A': 77.24651209325512, 'B': 90.81170061393325, 'C': 78.43345571343316} | {'A': 121.65347103895924, 'B': 135.30627543932593, 'C': 122.83690299162194} | {'A': 255.02290824365164, 'B': 268.76461832126836, 'C': 256.2028492466015} |
| Policy          | {'A': '1', 'B': '1', 'C': '1'}                                            | {'A': '1', 'B': '1', 'C': '1'}                                            | {'A': '1', 'B': '2', 'C': '1'}                                           | {'A': '1', 'B': '2', 'C': '1'}                                            | {'A': '1', 'B': '2', 'C': '1'}                                              | {'A': '1', 'B': '2', 'C': '1'}                                              | {'A': '1', 'B': '2', 'C': '1'}                                             | {'A': '1', 'B': '2', 'C': '1'}                                             | {'A': '1', 'B': '2', 'C': '1'}                                            | {'A': '1', 'B': '2', 'C': '1'}                                             | {'A': '1', 'B': '2', 'C': '2'}                                              | {'A': '1', 'B': '2', 'C': '2'}                                            | {'A': '1', 'B': '2', 'C': '2'}                                            | {'A': '1', 'B': '2', 'C': '2'}                                           | {'A': '1', 'B': '2', 'C': '2'}                                             | {'A': '2', 'B': '2', 'C': '2'}                                           | {'A': '2', 'B': '2', 'C': '2'}                                           | {'A': '2', 'B': '2', 'C': '2'}                                              | {'A': '2', 'B': '2', 'C': '2'}                                             |


<h1>
Observations
</h1>

<ul>
  <li>
  The expected reward of both algorithms are really close to make any significant observation.But consistently, the Gauss Seidel method seems to give a slighly higher expected reward for the same policy when compared to value iteration.
  </li>
  <li>
  The optimal policy is identical in all cases for both algorithms.
  </li>
</ul>

# Submit to AIcrowd 🚀

In [ ]:
!DATASET_PATH=$AICROWD_DATASET_PATH aicrowd notebook submit -c iit-m-rl-assignment-2-taxi -a assets